In [1]:
"""
This script is used to generate all possible combination of Options 
and store the results in separate Excel files.
Files are named by the combination of `OPT` inside `Options` sheet.
For example, in part 1
"1_1_1_1_1_1_1_1_1_1_1.xlsx" represents
['Massivbauweise', 'Mit UG', 'Beheizt', 'Mit abgehängte Installationsdecke', 'Mit abgehängte Installationsdecke', 'Bodenbelag mit Parkett', 'Bodenbelag mit Parkett', 'Mit Dämmung', 'Betonwand', 'Flachdach', 'Ja']

Author: Gul Sena Altintas
Modified from Ao Chen. Place: Zweistein.
"""

'\nThis script is used to generate all possible combination of Options \nand store the results in separate Excel files.\nFiles are named by the combination of `OPT` inside `Options` sheet.\nFor example, in part 1\n"1_1_1_1_1_1_1_1_1_1_1.xlsx" represents\n[\'Massivbauweise\', \'Mit UG\', \'Beheizt\', \'Mit abgehängte Installationsdecke\', \'Mit abgehängte Installationsdecke\', \'Bodenbelag mit Parkett\', \'Bodenbelag mit Parkett\', \'Mit Dämmung\', \'Betonwand\', \'Flachdach\', \'Ja\']\n\nAuthor: Gul Sena Altintas\nModified from Ao Chen. Place: Zweistein.\n'

In [48]:
# uncomment to install missing packages
# ! pip install xlwings pandas openpyxl numpy

In [2]:
import xlwings as xw
from openpyxl import Workbook, load_workbook
import pandas as pd
from datetime import date
from pandas import ExcelWriter
import re
import itertools
import numpy as np

Currently, processing of two parts are implemented, if in the future more parts are added define the following variables:

    part_no = x
    opt_range_x: (start_row - 1, end_row - 1, start_col -1, end_column - 1)
        where this is defined in the Options sheet
    opt_ranges = [..., opt_range_x]
    target_range_x = excel range of the calculated target table
    target_ranges = [..., target_range_x]
    
    -1 because we need the python indices
    
Excel format:
- Conditions must be defined as `na` for no condition, `ONLY IF CONDITIONED_CELL = CONDITIONED_VAL -->`.
- For each cell, `OPT` must start from 1 and be incremented.

In [71]:
excel_name = '031122_OptiBat_v4.xlsx' # TODO: change excel name
part_no = 2 # Change based on which part you want to run

opt_range_1 = (2, 24, 2, 6)
opt_range_2 = (27, 67, 2, 6)
opt_ranges = [opt_range_1, opt_range_2]

target_range_1 = ('M4:AL16')
target_range_2 = ('M25:AL37')
target_ranges = [target_range_1, target_range_2]

optbat_db = pd.ExcelFile(excel_name)

Today = date.today().strftime("%d_%b_%Y")
results_path = f'{Today}_part{part_no}_v2_results.xlsx' # TODO: change results name as needed

In [4]:
part = opt_ranges[part_no - 1]
target_range = target_ranges[part_no - 1]
    
Sheet_Options_df = optbat_db.parse('Options', header=None)
Sheet_Options_df = Sheet_Options_df.loc[part[0]: part[1], part[2]: part[3]]
Sheet_Options_df.columns = list(Sheet_Options_df.loc[part[0], :])
Sheet_Options_df = Sheet_Options_df.loc[part[0]+1:, :]
Sheet_Options_df = Sheet_Options_df.reset_index(drop=True)

In [5]:
Sheet_Options_df

Condition  Cell OPT  \
0                                  na   G25   1   
1                                  na   G25   2   
2                                  na   G25   3   
3                                  na   G26   1   
4                                  na   G26   2   
5            ONLY IF G26 = Mit UG -->   G27   1   
6            ONLY IF G26 = Mit UG -->   G27   2   
7                                  na   G28   1   
8                                  na   G28   2   
9                                  na   G28   3   
10                                 na   G28   4   
11           ONLY IF G26 = Mit UG -->  G29    1   
12           ONLY IF G26 = Mit UG -->  G29    2   
13           ONLY IF G26 = Mit UG -->  G29    3   
14           ONLY IF G26 = Mit UG -->  G29    4   
15                                 na   G30   1   
16                                 na   G30   2   
17                                 na   G31   1   
18                                 na   G31   2   
19   ONLY IF G25 = Massivbauweise -->   G32   1   
20   ONLY IF G25 = Massivbauweise -->   G32   2   
21                                 na   G33   1   
22                                 na   G34   1   
23                                 na   G34   2   
24                                 na   G34   3   
25                                 na   G34   4   
26                                 na   G34   5   
27                                 na   G34   6   
28                                 na   G34   7   
29                                 na   G34   8   
30                                 na   G35   1   
31                                 na   G35   2   
32        ONLY IF G35 = Flachdach -->  G36    1   
33        ONLY IF G35 = Flachdach -->  G36    2   
34        ONLY IF G35 = Flachdach -->   G37   1   
35        ONLY IF G35 = Flachdach -->   G37   2   
36                                 na   G38   1   
37                                 na   G38   2   

                                         Options  
0                                 Massivbauweise  
1                                 Leichtbauweise  
2                                  Mischbauweise  
3                                         Mit UG  
4                                        Ohne UG  
5                           Dach unter Terrain 1  
6                           Dach unter Terrain 2  
7              Mit abgehängte Installationsdecke  
8   Mit abgehängte Installationsdecke-Mischbau 1  
9   Mit abgehängte Installationsdecke-Mischbau 2  
10                             Ohne Installation  
11             Mit abgehängte Installationsdecke  
12  Mit abgehängte Installationsdecke-Mischbau 1  
13  Mit abgehängte Installationsdecke-Mischbau 2  
14                             Ohne Installation  
15               Decke über Terrain Bodenbelag 1  
16               Decke über Terrain Bodenbelag 2  
17              Decke unter Terrain Bodenbelag 1  
18              Decke unter Terrain Bodenbelag 2  
19                                     Betonwand  
20                                 Backsteinwand  
21                     Aussenwand über Terrain 1  
22          Aussenwand über Terrain Bekleidung 1  
23          Aussenwand über Terrain Bekleidung 2  
24          Aussenwand über Terrain Bekleidung 3  
25          Aussenwand über Terrain Bekleidung 4  
26          Aussenwand über Terrain Bekleidung 5  
27          Aussenwand über Terrain Bekleidung 6  
28          Aussenwand über Terrain Bekleidung 7  
29          Aussenwand über Terrain Bekleidung 8  
30                                     Flachdach  
31                                Geneigtes Dach  
32                                        Dach 1  
33                                        Dach 2  
34                             Dach Eindeckung 1  
35                             Dach Eindeckung 2  
36                                            Ja  
37                                          Nein

In [6]:
Options_list = list(Sheet_Options_df['Options'])
Options_position_list = [x.strip() for x in list(Sheet_Options_df['Cell'])]
Options_condition_list = [x.strip() for x in list(Sheet_Options_df['Condition'])]
Options_opt_list = list(Sheet_Options_df['OPT'])

conditioned_on = ['na' if type(i) != str or not i.startswith('ONLY IF') else re.split(r'ONLY IF | =', i)[1] for i in Options_condition_list ]
condition = ['na' if type(i) != str or not i.startswith('ONLY IF') else re.split(r'ONLY IF | = | --', i)[2] for i in Options_condition_list ]


In [7]:
arrays = [
    Options_position_list,
    Options_opt_list
]
tuples = list(zip(*arrays))
index = pd.MultiIndex.from_tuples(tuples, names=["Cell", "OPT"])

In [8]:
Options_df = pd.DataFrame({'Options': Options_list, 'Conditioned_on': conditioned_on, 
                           'Condition': condition,}, index=index)
condition_codes = ['na' if x == 'na' else 
                   Options_df.loc[x][Options_df.loc[x, 'Options'] == cond].index[0] 
                   for (x, cond) in zip(conditioned_on, condition)]
Options_df['Condition_Code'] = condition_codes

In [9]:
def get_groups(options:pd.DataFrame, include_keys):
    tmp = options.groupby(level=0, sort=False).count()['Options']
    groups = [[(ind, x) for x in range(1, i+1)] for (ind, i) in zip(tmp.index, tmp) if ind in include_keys]
    return groups

tmp = Options_df.groupby(level=0, sort=False).count()['Options']
groups = [[(ind, x) for x in range(1, i+1)] for (ind, i) in zip(tmp.index, tmp)]


In [72]:
# linux
# wb = load_workbook(excel_name)
# sheet_Gebäude = wb['Gebäude']

# windows
wb = xw.Book(excel_name)
sheet_Gebäude = wb.sheets['Gebäude']


In [70]:
def process(ws, cells: tuple, options: pd.DataFrame):
    ''' 
    cells: eg. 
    (('G4', 1), ('G5', 1), ('G6', 1), ('G7', 1), ('G8', 1), 
    ('G9', 1), ('G10', 1), ('G11', 1), ('G12', 1), ('G13', 1), 
    ('G14', 2))
    
    Warning: Note that the function as it is may result in faulty behavior
    if any cell has a dependency for a cell below it (eg. G33 depends on G34)
    
    returns:
        target_name (str): sheet_name in the form 1_2_1_.. eg where 1, 2's correspond to opt
        description (str): the options concatenated by ,
        df (pd.DataFrame): calculated values from the original sheet, target range is chosen in 
            the beginning of the notebook
        
     '''
    targets = []
    description = ''
    # for each cell, we check if the conditions are met
    for cell in cells:
        cond_cell = options.loc[cell, 'Conditioned_on']
        # if the cell depends on another cell, check if the value of the dependent cell 
        # is equal to the value that allows this specific value
        # if the condition is not met, this cell is skipped, its results are not written to
        # target_name (the name of the sheet) or the description
        if cond_cell != 'na':
            cond = options.loc[cell, 'Condition']
            if ws.range(cond_cell).value != cond:
                continue
        # set cell value
        ws.range(cell[0]).value = options.loc[cell, 'Options']
        description += options.loc[cell, 'Options'] + ', '
        targets.append(cell[1])
    target_name = '_'.join([str(x) for x in targets])
    return target_name, description, pd.DataFrame(sheet_Gebäude.range(target_range).value)
                           

**Comment**: Please note that the following operation performs unnecessary computations (in the order of $\Pi group^{dependencies}$ hence it is significantly slow, as we actually don't need to check some cases, ie. any of G6, 7, 10, 11 when G5 is not 'Mit UG'. However, the other way around is prone to potential human mistakes and requires everything to be hard-coded.

In [18]:
all_combs = list(itertools.product(*groups))
all_combs.reverse()
len(all_combs)

196608

In [68]:
# filter unnecessary combinations
to_process = []
for comb in all_combs:
    l = Options_df.loc[[*comb]]
    conds = [(x, y) for (x, y) in zip(l['Conditioned_on'], l['Condition_Code']) if x != 'na']
    valid = True
    for c in conds:
        if c not in comb:
            valid = False
            break
    if valid:
        to_process.append(comb)
print(f'Filtering completed, will process {len(to_process)} combinations')

Filtering completed, will process 16384 combinations


In [76]:
with open('process.txt', 'w') as f:
    for t in to_process:
        f.write(str(t)+'\n')

In [81]:
error_dict = {-2146826281:'#N/A', -2146826246:'#N/A'} # for xlwings #n/a values
se = set()
to_process.reverse()
with ExcelWriter(results_path) as writer:
    for (i, comb) in enumerate(to_process):
        target_name, description, df = process(sheet_Gebäude, comb, Options_df)
        df.loc[len(df), 0] = description
        df.replace(to_replace=error_dict, inplace=True) 
        se.add(target_name)
        print(i, description)
        df.to_excel(writer, sheet_name=target_name, header=None, index=None, na_rep='')
print(f'Written a total of {len(se)} sheets.')

0 Massivbauweise, Mit UG, Dach unter Terrain 1, Mit abgehängte Installationsdecke, Mit abgehängte Installationsdecke, Decke über Terrain Bodenbelag 1, Decke unter Terrain Bodenbelag 1, Betonwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 1, Flachdach, Dach 1, Dach Eindeckung 1, Ja, 
1 Massivbauweise, Mit UG, Dach unter Terrain 1, Mit abgehängte Installationsdecke, Mit abgehängte Installationsdecke, Decke über Terrain Bodenbelag 1, Decke unter Terrain Bodenbelag 1, Betonwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 1, Flachdach, Dach 1, Dach Eindeckung 1, Nein, 
2 Massivbauweise, Mit UG, Dach unter Terrain 1, Mit abgehängte Installationsdecke, Mit abgehängte Installationsdecke, Decke über Terrain Bodenbelag 1, Decke unter Terrain Bodenbelag 1, Betonwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 1, Flachdach, Dach 1, Dach Eindeckung 2, Ja, 
3 Massivbauweise, Mit UG, Dach unter Terrain 1, Mit abgehängte Installationsdecke, Mit

27 Massivbauweise, Mit UG, Dach unter Terrain 1, Mit abgehängte Installationsdecke, Mit abgehängte Installationsdecke, Decke über Terrain Bodenbelag 1, Decke unter Terrain Bodenbelag 1, Betonwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 4, Flachdach, Dach 1, Dach Eindeckung 2, Nein, 
28 Massivbauweise, Mit UG, Dach unter Terrain 1, Mit abgehängte Installationsdecke, Mit abgehängte Installationsdecke, Decke über Terrain Bodenbelag 1, Decke unter Terrain Bodenbelag 1, Betonwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 4, Flachdach, Dach 2, Dach Eindeckung 1, Ja, 
29 Massivbauweise, Mit UG, Dach unter Terrain 1, Mit abgehängte Installationsdecke, Mit abgehängte Installationsdecke, Decke über Terrain Bodenbelag 1, Decke unter Terrain Bodenbelag 1, Betonwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 4, Flachdach, Dach 2, Dach Eindeckung 1, Nein, 
30 Massivbauweise, Mit UG, Dach unter Terrain 1, Mit abgehängte Installationsdeck

54 Massivbauweise, Mit UG, Dach unter Terrain 1, Mit abgehängte Installationsdecke, Mit abgehängte Installationsdecke, Decke über Terrain Bodenbelag 1, Decke unter Terrain Bodenbelag 1, Betonwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 7, Flachdach, Dach 2, Dach Eindeckung 2, Ja, 
55 Massivbauweise, Mit UG, Dach unter Terrain 1, Mit abgehängte Installationsdecke, Mit abgehängte Installationsdecke, Decke über Terrain Bodenbelag 1, Decke unter Terrain Bodenbelag 1, Betonwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 7, Flachdach, Dach 2, Dach Eindeckung 2, Nein, 
56 Massivbauweise, Mit UG, Dach unter Terrain 1, Mit abgehängte Installationsdecke, Mit abgehängte Installationsdecke, Decke über Terrain Bodenbelag 1, Decke unter Terrain Bodenbelag 1, Betonwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 8, Flachdach, Dach 1, Dach Eindeckung 1, Ja, 
57 Massivbauweise, Mit UG, Dach unter Terrain 1, Mit abgehängte Installationsdecke,

81 Massivbauweise, Mit UG, Dach unter Terrain 1, Mit abgehängte Installationsdecke, Mit abgehängte Installationsdecke, Decke über Terrain Bodenbelag 1, Decke unter Terrain Bodenbelag 1, Backsteinwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 3, Flachdach, Dach 1, Dach Eindeckung 1, Nein, 
82 Massivbauweise, Mit UG, Dach unter Terrain 1, Mit abgehängte Installationsdecke, Mit abgehängte Installationsdecke, Decke über Terrain Bodenbelag 1, Decke unter Terrain Bodenbelag 1, Backsteinwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 3, Flachdach, Dach 1, Dach Eindeckung 2, Ja, 
83 Massivbauweise, Mit UG, Dach unter Terrain 1, Mit abgehängte Installationsdecke, Mit abgehängte Installationsdecke, Decke über Terrain Bodenbelag 1, Decke unter Terrain Bodenbelag 1, Backsteinwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 3, Flachdach, Dach 1, Dach Eindeckung 2, Nein, 
84 Massivbauweise, Mit UG, Dach unter Terrain 1, Mit abgehängte Insta

108 Massivbauweise, Mit UG, Dach unter Terrain 1, Mit abgehängte Installationsdecke, Mit abgehängte Installationsdecke, Decke über Terrain Bodenbelag 1, Decke unter Terrain Bodenbelag 1, Backsteinwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 6, Flachdach, Dach 2, Dach Eindeckung 1, Ja, 
109 Massivbauweise, Mit UG, Dach unter Terrain 1, Mit abgehängte Installationsdecke, Mit abgehängte Installationsdecke, Decke über Terrain Bodenbelag 1, Decke unter Terrain Bodenbelag 1, Backsteinwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 6, Flachdach, Dach 2, Dach Eindeckung 1, Nein, 
110 Massivbauweise, Mit UG, Dach unter Terrain 1, Mit abgehängte Installationsdecke, Mit abgehängte Installationsdecke, Decke über Terrain Bodenbelag 1, Decke unter Terrain Bodenbelag 1, Backsteinwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 6, Flachdach, Dach 2, Dach Eindeckung 2, Ja, 
111 Massivbauweise, Mit UG, Dach unter Terrain 1, Mit abgehängte Ins

...

16242 Massivbauweise, Mit UG, Dach unter Terrain 2, Ohne Installation, Ohne Installation, Decke über Terrain Bodenbelag 2, Decke unter Terrain Bodenbelag 1, Backsteinwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 7, Flachdach, Dach 1, Dach Eindeckung 2, Ja, 
16243 Massivbauweise, Mit UG, Dach unter Terrain 2, Ohne Installation, Ohne Installation, Decke über Terrain Bodenbelag 2, Decke unter Terrain Bodenbelag 1, Backsteinwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 7, Flachdach, Dach 1, Dach Eindeckung 2, Nein, 
16244 Massivbauweise, Mit UG, Dach unter Terrain 2, Ohne Installation, Ohne Installation, Decke über Terrain Bodenbelag 2, Decke unter Terrain Bodenbelag 1, Backsteinwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 7, Flachdach, Dach 2, Dach Eindeckung 1, Ja, 
16245 Massivbauweise, Mit UG, Dach unter Terrain 2, Ohne Installation, Ohne Installation, Decke über Terrain Bodenbelag 2, Decke unter Terrain Bodenbelag 1, B

16272 Massivbauweise, Mit UG, Dach unter Terrain 2, Ohne Installation, Ohne Installation, Decke über Terrain Bodenbelag 2, Decke unter Terrain Bodenbelag 2, Betonwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 3, Flachdach, Dach 1, Dach Eindeckung 1, Ja, 
16273 Massivbauweise, Mit UG, Dach unter Terrain 2, Ohne Installation, Ohne Installation, Decke über Terrain Bodenbelag 2, Decke unter Terrain Bodenbelag 2, Betonwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 3, Flachdach, Dach 1, Dach Eindeckung 1, Nein, 
16274 Massivbauweise, Mit UG, Dach unter Terrain 2, Ohne Installation, Ohne Installation, Decke über Terrain Bodenbelag 2, Decke unter Terrain Bodenbelag 2, Betonwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 3, Flachdach, Dach 1, Dach Eindeckung 2, Ja, 
16275 Massivbauweise, Mit UG, Dach unter Terrain 2, Ohne Installation, Ohne Installation, Decke über Terrain Bodenbelag 2, Decke unter Terrain Bodenbelag 2, Betonwand, Au

16302 Massivbauweise, Mit UG, Dach unter Terrain 2, Ohne Installation, Ohne Installation, Decke über Terrain Bodenbelag 2, Decke unter Terrain Bodenbelag 2, Betonwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 6, Flachdach, Dach 2, Dach Eindeckung 2, Ja, 
16303 Massivbauweise, Mit UG, Dach unter Terrain 2, Ohne Installation, Ohne Installation, Decke über Terrain Bodenbelag 2, Decke unter Terrain Bodenbelag 2, Betonwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 6, Flachdach, Dach 2, Dach Eindeckung 2, Nein, 
16304 Massivbauweise, Mit UG, Dach unter Terrain 2, Ohne Installation, Ohne Installation, Decke über Terrain Bodenbelag 2, Decke unter Terrain Bodenbelag 2, Betonwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 7, Flachdach, Dach 1, Dach Eindeckung 1, Ja, 
16305 Massivbauweise, Mit UG, Dach unter Terrain 2, Ohne Installation, Ohne Installation, Decke über Terrain Bodenbelag 2, Decke unter Terrain Bodenbelag 2, Betonwand, Au

16332 Massivbauweise, Mit UG, Dach unter Terrain 2, Ohne Installation, Ohne Installation, Decke über Terrain Bodenbelag 2, Decke unter Terrain Bodenbelag 2, Backsteinwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 2, Flachdach, Dach 2, Dach Eindeckung 1, Ja, 
16333 Massivbauweise, Mit UG, Dach unter Terrain 2, Ohne Installation, Ohne Installation, Decke über Terrain Bodenbelag 2, Decke unter Terrain Bodenbelag 2, Backsteinwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 2, Flachdach, Dach 2, Dach Eindeckung 1, Nein, 
16334 Massivbauweise, Mit UG, Dach unter Terrain 2, Ohne Installation, Ohne Installation, Decke über Terrain Bodenbelag 2, Decke unter Terrain Bodenbelag 2, Backsteinwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 2, Flachdach, Dach 2, Dach Eindeckung 2, Ja, 
16335 Massivbauweise, Mit UG, Dach unter Terrain 2, Ohne Installation, Ohne Installation, Decke über Terrain Bodenbelag 2, Decke unter Terrain Bodenbelag 2, B

16362 Massivbauweise, Mit UG, Dach unter Terrain 2, Ohne Installation, Ohne Installation, Decke über Terrain Bodenbelag 2, Decke unter Terrain Bodenbelag 2, Backsteinwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 6, Flachdach, Dach 1, Dach Eindeckung 2, Ja, 
16363 Massivbauweise, Mit UG, Dach unter Terrain 2, Ohne Installation, Ohne Installation, Decke über Terrain Bodenbelag 2, Decke unter Terrain Bodenbelag 2, Backsteinwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 6, Flachdach, Dach 1, Dach Eindeckung 2, Nein, 
16364 Massivbauweise, Mit UG, Dach unter Terrain 2, Ohne Installation, Ohne Installation, Decke über Terrain Bodenbelag 2, Decke unter Terrain Bodenbelag 2, Backsteinwand, Aussenwand über Terrain 1, Aussenwand über Terrain Bekleidung 6, Flachdach, Dach 2, Dach Eindeckung 1, Ja, 
16365 Massivbauweise, Mit UG, Dach unter Terrain 2, Ohne Installation, Ohne Installation, Decke über Terrain Bodenbelag 2, Decke unter Terrain Bodenbelag 2, B